In this notebook, we'll look at featurizing fatigue to see if we can get lift on our models through this.
The Sipko paper indicates that fatigue can be featurized by:

* Number of matches played in last 3 days
* Indicator for whether this is the first match back after retiring from one 

In [1]:
from fetch.match_results import read_joined 

df, player_mapping, inverse_player_mapping = read_joined()

/Users/siddhantjagadish/Documents/DataProjects/tennis_modeling/tennis_modeling/lib/python2.7/site-packages/IPython/core/interactiveshell.py:2818: DtypeWarning: Columns (14) have mixed types. Specify dtype option on import or set low_memory=False.
  if self.run_code(code, result):


In [2]:
df.sort(['date', 'round'], inplace=True)

/Users/siddhantjagadish/Documents/DataProjects/tennis_modeling/tennis_modeling/lib/python2.7/site-packages/ipykernel_launcher.py:1: FutureWarning: sort(columns=....) is deprecated, use sort_values(by=.....)
  """Entry point for launching an IPython kernel.


#### True ELO Model

$\theta_{j, t + 1} = \theta_t + \alpha(y_t - \hat{y}_t)x_j$

From 538, one setting that works well is: 

$\alpha = \frac{250}{[M + 5]^{0.4}}$

Is this particular to using baseline of $\theta=1500$?

In [4]:
import pandas as pd

pd.set_option('display.max_rows', 999)
df.iloc[0]

atp                                             1
avgl                                          NaN
avgw                                          NaN
b&wl                                          NaN
b&ww                                          NaN
b365l                                         NaN
b365w                                         NaN
best of                                         3
cbl                                           NaN
cbw                                           NaN
comment                                 Completed
court                                     Outdoor
date                          2000-01-03 00:00:00
exl                                           NaN
exw                                           NaN
gbl                                           NaN
gbw                                           NaN
iwl                                           NaN
iww                                           NaN
l1                                              4


In [29]:
import numpy as np
from collections import defaultdict

beta = {k: 1500. for k in inverse_player_mapping.keys()}
player_count = defaultdict(lambda: 0)

SURFACE_WEIGHTS = {
    'Clay': 1.0,
    'Hard': 0.4,
    'Grass': 0.0,
    'Indoor': 0.6
}

def elo(x):
    return 1. / (1. + 10. ** (-x / 400.))

def process_row(row, beta, beta_history, preds):
    p1 = row['p1_idx']
    p2 = row['p2_idx']
    match_id = row['match_id']
        
    pred = elo(beta[p1] - beta[p2]) 
    preds.append((match_id, pred))
    print "%s playing %s on %s, pred: %f, winner: %s" % (
        row['p1_name'],
        row['p2_name'],
        str(row['date']),
        pred,
        row['winner']
    )

    # TODO: Can tune these...
    sw = SURFACE_WEIGHTS[row['__surface__']] 
    k1 = sw * 250. / ((player_count[p1] + 5.) ** 0.4)
    k2 = sw * 250. / ((player_count[p2] + 5.) ** 0.4)

    new_beta1 = beta[p1] + k1 * (row['y'] - pred)
    new_beta2 = beta[p2] + k2 * (pred - row['y'])
    beta[p1] = new_beta1
    beta[p2] = new_beta2
    beta_history.append((match_id, new_beta1, new_beta2))

    player_count[p1] += 1
    player_count[p2] += 1
    return beta, beta_history, preds
    
def elo_backfill(df):
    beta_history = []
    preds = []
    beta = {k: 1500. for k in inverse_player_mapping.keys()}
    player_count = defaultdict(lambda: 0)
    for _, row in df.iterrows():
        beta, beta_history, preds = process_row(row, beta, beta_history, preds)
    return beta, beta_history, preds

In [30]:
beta, beta_history, preds = elo_backfill(df)

Dosedel S. playing Ljubicic I. on 2000-01-03 00:00:00, pred: 0.500000, winner: Dosedel S.
Clement A. playing Enqvist T. on 2000-01-03 00:00:00, pred: 0.500000, winner: Enqvist T.
Baccanello P. playing Escude N. on 2000-01-03 00:00:00, pred: 0.500000, winner: Escude N.
Federer R. playing Knippschild J. on 2000-01-03 00:00:00, pred: 0.500000, winner: Federer R.
Fromberg R. playing Woodbridge T. on 2000-01-03 00:00:00, pred: 0.500000, winner: Fromberg R.
Arthurs W. playing Gambill J.M. on 2000-01-03 00:00:00, pred: 0.500000, winner: Gambill J.M.
Grosjean S. playing Ilie A. on 2000-01-03 00:00:00, pred: 0.500000, winner: Grosjean S.
Balcells J. playing Henman T. on 2000-01-03 00:00:00, pred: 0.500000, winner: Henman T.
Hewitt L. playing Woodforde M. on 2000-01-03 00:00:00, pred: 0.500000, winner: Hewitt L.
Lisnard J. playing Tebbutt M. on 2000-01-03 00:00:00, pred: 0.500000, winner: Lisnard J.
Martin A. playing Spadea V. on 2000-01-03 00:00:00, pred: 0.500000, winner: Martin A.
Draper S. p

Fromberg R. playing Stark J. on 2000-02-28 00:00:00, pred: 0.533678, winner: Fromberg R.
Alonso J. playing Gambill J.M. on 2000-02-28 00:00:00, pred: 0.426193, winner: Gambill J.M.
Alami K. playing Gimelstob J. on 2000-02-28 00:00:00, pred: 0.581487, winner: Gimelstob J.
Goldstein P. playing Pavel A. on 2000-02-28 00:00:00, pred: 0.555125, winner: Goldstein P.
Hipfl M. playing Srichaphan P. on 2000-02-28 00:00:00, pred: 0.485938, winner: Hipfl M.
Chang M. playing Ilie A. on 2000-02-28 00:00:00, pred: 0.672066, winner: Ilie A.
Black B. playing Koubek S. on 2000-02-28 00:00:00, pred: 0.359174, winner: Koubek S.
Malisse X. playing van Lottum J. on 2000-02-28 00:00:00, pred: 0.491801, winner: Malisse X.
Mamiit C. playing Mirnyi M. on 2000-02-28 00:00:00, pred: 0.552910, winner: Mamiit C.
Gumy H. playing Rafter P. on 2000-02-28 00:00:00, pred: 0.468210, winner: Rafter P.
Sa A. playing Szymanski J. on 2000-02-28 00:00:00, pred: 0.546020, winner: Sa A.
Roddick A. playing Tieleman L. on 2000-0

Dewulf F. playing Ulihrach B. on 2000-05-01 00:00:00, pred: 0.495242, winner: Ulihrach B.
Bastl G. playing Garcia M. on 2000-05-01 00:00:00, pred: 0.522444, winner: Bastl G.
Blanco G. playing Stanoytchev O. on 2000-05-01 00:00:00, pred: 0.349849, winner: Blanco G.
Chela J.I. playing Gustafsson M. on 2000-05-01 00:00:00, pred: 0.706300, winner: Chela J.I.
Coria G. playing Rochus C. on 2000-05-01 00:00:00, pred: 0.570931, winner: Coria G.
Kafelnikov Y. playing Sanguinetti D. on 2000-05-01 00:00:00, pred: 0.663757, winner: Kafelnikov Y.
Diaz J. playing Marin J.A. on 2000-05-01 00:00:00, pred: 0.341860, winner: Marin J.A.
Bruguera S. playing Martin A. on 2000-05-01 00:00:00, pred: 0.679143, winner: Martin A.
Goellner M.K. playing Moya C. on 2000-05-01 00:00:00, pred: 0.195600, winner: Moya C.
Gaudenzi A. playing Portas A. on 2000-05-01 00:00:00, pred: 0.385934, winner: Portas A.
Hipfl M. playing Puerta M. on 2000-05-01 00:00:00, pred: 0.167526, winner: Puerta M.
Balcells J. playing Rios M.

Johansson T. playing Meligeni F. on 2000-06-26 00:00:00, pred: 0.405187, winner: Johansson T.
Federer R. playing Kafelnikov Y. on 2000-06-26 00:00:00, pred: 0.348075, winner: Kafelnikov Y.
Koubek S. playing Voinea A. on 2000-06-26 00:00:00, pred: 0.759794, winner: Koubek S.
Kohlmann M. playing Krajicek R. on 2000-06-26 00:00:00, pred: 0.391611, winner: Krajicek R.
Kuerten G. playing Woodruff C. on 2000-06-26 00:00:00, pred: 0.957100, winner: Kuerten G.
Lareau S. playing Russell M. on 2000-06-26 00:00:00, pred: 0.396039, winner: Lareau S.
Lee M. playing Marin J.A. on 2000-06-26 00:00:00, pred: 0.480621, winner: Lee M.
Levy H. playing Stoltenberg J. on 2000-06-26 00:00:00, pred: 0.265223, winner: Levy H.
Alami K. playing Llodra M. on 2000-06-26 00:00:00, pred: 0.548648, winner: Llodra M.
Eschauer W. playing Martin A. on 2000-06-26 00:00:00, pred: 0.534386, winner: Martin A.
Mirnyi M. playing Ulihrach B. on 2000-06-26 00:00:00, pred: 0.539937, winner: Mirnyi M.
MacLagan M. playing Nestor 

Agassi A. playing Vicente F. on 2000-08-07 00:00:00, pred: 0.683843, winner: Vicente F.
Clement A. playing Kafelnikov Y. on 2000-08-07 00:00:00, pred: 0.329734, winner: Clement A.
Enqvist T. playing Mirnyi M. on 2000-08-07 00:00:00, pred: 0.660972, winner: Enqvist T.
Henman T. playing Sampras P. on 2000-08-07 00:00:00, pred: 0.522361, winner: Henman T.
Koubek S. playing Kuerten G. on 2000-08-07 00:00:00, pred: 0.075608, winner: Kuerten G.
Bjorkman J. playing Martin T. on 2000-08-07 00:00:00, pred: 0.515713, winner: Martin T.
Safin M. playing Santoro F. on 2000-08-07 00:00:00, pred: 0.802688, winner: Santoro F.
Dosedel S. playing Squillari F. on 2000-08-07 00:00:00, pred: 0.171014, winner: Squillari F.
Philippoussis M. playing Vicente F. on 2000-08-07 00:00:00, pred: 0.711545, winner: Vicente F.
Clement A. playing Squillari F. on 2000-08-07 00:00:00, pred: 0.214132, winner: Clement A.
Enqvist T. playing Vicente F. on 2000-08-07 00:00:00, pred: 0.769412, winner: Enqvist T.
Henman T. play

...

Brown D. playing Murray A. on 2017-07-05 00:00:00, pred: 0.042339, winner: Murray A.
Herbert P.H. playing Paire B. on 2017-07-05 00:00:00, pred: 0.342614, winner: Paire B.
Nadal R. playing Young D. on 2017-07-05 00:00:00, pred: 0.958993, winner: Nadal R.
Darcis S. playing Ferrer D. on 2017-07-06 00:00:00, pred: 0.220105, winner: Ferrer D.
Baghdatis M. playing Dimitrov G. on 2017-07-06 00:00:00, pred: 0.277267, winner: Dimitrov G.
Isner J. playing Sela D. on 2017-07-06 00:00:00, pred: 0.829135, winner: Sela D.
Kukushkin M. playing Zverev M. on 2017-07-06 00:00:00, pred: 0.427143, winner: Zverev M.
Del Potro J.M. playing Gulbis E. on 2017-07-06 00:00:00, pred: 0.864172, winner: Gulbis E.
Edmund K. playing Monfils G. on 2017-07-06 00:00:00, pred: 0.243155, winner: Monfils G.
Djokovic N. playing Pavlasek A. on 2017-07-06 00:00:00, pred: 0.987994, winner: Djokovic N.
Mannarino A. playing Sugita Y. on 2017-07-06 00:00:00, pred: 0.517323, winner: Mannarino A.
Simon G. playing Thiem D. on 2017

Medvedev D. playing Shapovalov D. on 2017-08-28 00:00:00, pred: 0.405225, winner: Shapovalov D.
Kwiatkowski T.S. playing Zverev M. on 2017-08-28 00:00:00, pred: 0.349195, winner: Zverev M.
Muller G. playing Tomic B. on 2017-08-28 00:00:00, pred: 0.675806, winner: Muller G.
Kokkinakis T. playing Tipsarevic J. on 2017-08-28 00:00:00, pred: 0.425494, winner: Tipsarevic J.
Querrey S. playing Simon G. on 2017-08-28 00:00:00, pred: 0.503998, winner: Querrey S.
Fucsovics M. playing Mahut N. on 2017-08-28 00:00:00, pred: 0.395538, winner: Mahut N.
Bemelmans R. playing Pouille L. on 2017-08-28 00:00:00, pred: 0.163089, winner: Pouille L.
Fabbiano T. playing Smith J.P. on 2017-08-28 00:00:00, pred: 0.415015, winner: Fabbiano T.
Sock J. playing Thompson J. on 2017-08-28 00:00:00, pred: 0.820666, winner: Thompson J.
Basilashvili N. playing Donaldson J. on 2017-08-28 00:00:00, pred: 0.547603, winner: Donaldson J.
Coric B. playing Vesely J. on 2017-08-28 00:00:00, pred: 0.539669, winner: Coric B.
Ki

Ferrer D. playing Mannarino A. on 2017-10-31 00:00:00, pred: 0.773539, winner: Mannarino A.
Krajinovic F. playing Querrey S. on 2017-10-31 00:00:00, pred: 0.247658, winner: Krajinovic F.
Carreno Busta P. playing Mahut N. on 2017-10-31 00:00:00, pred: 0.731923, winner: Mahut N.
Gojowczyk P. playing Thiem D. on 2017-10-31 00:00:00, pred: 0.161822, winner: Thiem D.
Isner J. playing Schwartzman D. on 2017-11-01 00:00:00, pred: 0.461458, winner: Isner J.
Haase R. playing Zverev A. on 2017-11-01 00:00:00, pred: 0.148599, winner: Haase R.
Cuevas P. playing Ramos-Vinolas A. on 2017-11-01 00:00:00, pred: 0.450500, winner: Cuevas P.
Lopez F. playing Pouille L. on 2017-11-01 00:00:00, pred: 0.357229, winner: Pouille L.
Anderson K. playing Verdasco F. on 2017-11-01 00:00:00, pred: 0.559325, winner: Verdasco F.
Chung H. playing Nadal R. on 2017-11-01 00:00:00, pred: 0.074392, winner: Nadal R.
Benneteau J. playing Tsonga J.W. on 2017-11-01 00:00:00, pred: 0.192272, winner: Benneteau J.
Del Potro J.M

Sela D. playing Youzhny M. on 2018-02-20 00:00:00, pred: 0.452764, winner: Youzhny M.
Fritz T. playing Querrey S. on 2018-02-20 00:00:00, pred: 0.357517, winner: Fritz T.
Krajinovic F. playing Sousa J. on 2018-02-20 00:00:00, pred: 0.466184, winner: Krajinovic F.
Djere L. playing Ivashka I. on 2018-02-20 00:00:00, pred: 0.651479, winner: Ivashka I.
Bemelmans R. playing Khachanov K. on 2018-02-20 00:00:00, pred: 0.290275, winner: Khachanov K.
Gaston H. playing Travaglia S. on 2018-02-20 00:00:00, pred: 0.528858, winner: Travaglia S.
Marterer M. playing Simon G. on 2018-02-20 00:00:00, pred: 0.172900, winner: Simon G.
Gombos N. playing Herbert P.H. on 2018-02-20 00:00:00, pred: 0.386508, winner: Herbert P.H.
Bellucci T. playing Fognini F. on 2018-02-20 00:00:00, pred: 0.291116, winner: Fognini F.
Andujar P. playing Melzer G. on 2018-02-20 00:00:00, pred: 0.512515, winner: Andujar P.
Estrella Burgos V. playing Kicker N. on 2018-02-20 00:00:00, pred: 0.576299, winner: Kicker N.
Ruud C. pla

Basilashvili N. playing Seppi A. on 2018-04-27 00:00:00, pred: 0.422163, winner: Seppi A.
Bedene A. playing Sonego L. on 2018-04-27 00:00:00, pred: 0.654672, winner: Bedene A.
Carreno Busta P. playing Dimitrov G. on 2018-04-27 00:00:00, pred: 0.335359, winner: Carreno Busta P.
Klizan M. playing Nadal R. on 2018-04-27 00:00:00, pred: 0.073940, winner: Nadal R.
Maden Y. playing Millman J. on 2018-04-28 00:00:00, pred: 0.377918, winner: Millman J.
Cecchinato M. playing Seppi A. on 2018-04-28 00:00:00, pred: 0.272051, winner: Cecchinato M.
Carreno Busta P. playing Tsitsipas S. on 2018-04-28 00:00:00, pred: 0.639885, winner: Tsitsipas S.
Goffin D. playing Nadal R. on 2018-04-28 00:00:00, pred: 0.160097, winner: Nadal R.
Bedene A. playing Millman J. on 2018-04-29 00:00:00, pred: 0.668278, winner: Millman J.
Cecchinato M. playing Millman J. on 2018-04-29 00:00:00, pred: 0.355533, winner: Cecchinato M.
Nadal R. playing Tsitsipas S. on 2018-04-29 00:00:00, pred: 0.925194, winner: Nadal R.
Baghd

In [31]:
from sklearn.metrics import roc_auc_score

MIN_TEST_DATE = '2015-01-01'
MAX_TEST_DATE = '2017-01-01'

df['pred'] = zip(*preds)[1]
rec_df = df[
    (df['date'] >= MIN_TEST_DATE) &
    (df['date'] < MAX_TEST_DATE) &
    (df['__surface__'] == 'Clay') &
    (~df['comment'].isin(['Retired', 'Walkover']))  # Remove retire from test set
]

In [32]:
roc_auc_score(rec_df['y'], rec_df['pred'])

0.76146226319930599

This is great performance!  Wow!!!

#### Tune ELO parameters